In [29]:
pip install transformers

In [30]:
pip install accelerate -U

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 297.4/297.4 kB 3.6 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl (196.0 MB)
  Using cached nvidia_nccl_cu12-2.19.3-py3-none-manylinux1_x86_64.whl (166.0 MB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-many

In [1]:
import pandas as pd
import numpy as np
import seaborn as sb
from matplotlib import pyplot as plt
from datetime import datetime
import string
from transformers import AutoTokenizer, AutoModelForSequenceClassification
from nltk.tokenize import TweetTokenizer
from scipy.special import softmax
from imblearn.over_sampling import RandomOverSampler
from tqdm import tqdm
import nltk
from tqdm import tqdm
import re
import torch
import os

In [10]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer, AutoConfig, AdamW, Trainer, TrainingArguments

In [2]:
data = pd.read_csv('preprocessed_data.csv')

In [3]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 287188 entries, 0 to 287187
Data columns (total 20 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   id                   287187 non-null  float64
 1   createdAt            287188 non-null  object 
 2   fullName             287149 non-null  object 
 3   userName             287188 non-null  object 
 4   profileImage         287188 non-null  object 
 5   fullText             287188 non-null  object 
 6   replyTo              287188 non-null  int64  
 7   lang                 287188 non-null  object 
 8   quoteCount           287188 non-null  int64  
 9   retweetCount         287188 non-null  int64  
 10  replyCount           287188 non-null  int64  
 11  likeCount            287188 non-null  int64  
 12  viewCount            103504 non-null  float64
 13  sentimentLabel1      1790 non-null    float64
 14  sentimentLabel2      1201 non-null    float64
 15  sentimentLabel3  

# RoBerta

In [4]:
labeled_data = data[data['sentimentLabelFinal'].notnull()]

In [5]:
labeled_data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 996 entries, 152428 to 153426
Data columns (total 20 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   id                   996 non-null    float64
 1   createdAt            996 non-null    object 
 2   fullName             996 non-null    object 
 3   userName             996 non-null    object 
 4   profileImage         996 non-null    object 
 5   fullText             996 non-null    object 
 6   replyTo              996 non-null    int64  
 7   lang                 996 non-null    object 
 8   quoteCount           996 non-null    int64  
 9   retweetCount         996 non-null    int64  
 10  replyCount           996 non-null    int64  
 11  likeCount            996 non-null    int64  
 12  viewCount            0 non-null      float64
 13  sentimentLabel1      996 non-null    float64
 14  sentimentLabel2      996 non-null    float64
 15  sentimentLabel3      996 non-null    

In [24]:
# oversample
X = labeled_data[['cleaned_tweet']]
y = labeled_data['sentimentLabelFinal']

# Initialize RandomOverSampler
ros = RandomOverSampler()

# Perform Random OverSampling
X_resampled, y_resampled = ros.fit_resample(X, y)

resampled_df = pd.DataFrame(X_resampled, columns=X.columns)
resampled_df['sentimentLabelFinal'] = y_resampled

print(resampled_df['sentimentLabelFinal'].value_counts())


sentimentLabelFinal
1.0    497
0.0    497
2.0    497
Name: count, dtype: int64


In [25]:
labeled_data = resampled_df

In [26]:
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
from sklearn.model_selection import train_test_split
from torch.utils.data import DataLoader, TensorDataset, RandomSampler, SequentialSampler
from tqdm import tqdm
from sklearn.metrics import classification_report

train_data, val_data = train_test_split(labeled_data, test_size=0.2, random_state=42)

# Load pre-trained RoBERTa tokenizer
MODEL = "cardiffnlp/twitter-roberta-base-sentiment-latest"
tokenizer = AutoTokenizer.from_pretrained(MODEL)
config = AutoConfig.from_pretrained(MODEL)

# Tokenize text data
train_encodings = tokenizer(list(train_data['cleaned_tweet']), truncation=True, padding=True, max_length=128, return_tensors='pt')
val_encodings = tokenizer(list(val_data['cleaned_tweet']), truncation=True, padding=True, max_length=128, return_tensors='pt')

# Convert labels to tensors of type torch.long
train_labels = torch.tensor(list(train_data['sentimentLabelFinal']), dtype=torch.long)
val_labels = torch.tensor(list(val_data['sentimentLabelFinal']), dtype=torch.long)

# Define TensorDatasets for training and validation
train_dataset = TensorDataset(train_encodings['input_ids'], train_encodings['attention_mask'], train_labels)
val_dataset = TensorDataset(val_encodings['input_ids'], val_encodings['attention_mask'], val_labels)

# Initialize the model
model = AutoModelForSequenceClassification.from_pretrained(MODEL, config=config)

batch_size = 32
epochs = 3
learning_rate = 2e-5

optimizer = AdamW(model.parameters(), lr=learning_rate)
loss_fn = nn.CrossEntropyLoss()

train_loader = DataLoader(train_dataset, batch_size=batch_size, sampler=RandomSampler(train_dataset))
val_loader = DataLoader(val_dataset, batch_size=batch_size, sampler=SequentialSampler(val_dataset))

Some weights of the model checkpoint at cardiffnlp/twitter-roberta-base-sentiment-latest were not used when initializing RobertaForSequenceClassification: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:429: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this w

In [ ]:
# Training loop
model.train()
for epoch in range(epochs):
    total_loss = 0
    for batch in tqdm(train_loader, desc=f'Epoch {epoch + 1}', unit='batches'):
        input_ids, attention_mask, labels = batch
        optimizer.zero_grad()
        logits = model(input_ids, attention_mask=attention_mask).logits
        loss = loss_fn(logits, labels)
        total_loss += loss.item()
        loss.backward()
        optimizer.step()
    print(f'Epoch {epoch + 1}, Loss: {total_loss / len(train_loader)}')

# Evaluation
model.eval()
all_preds, all_labels = [], []
with torch.no_grad():
    for batch in tqdm(val_loader, desc='Evaluation', unit='batches'):
        input_ids, attention_mask, labels = batch
        logits = model(input_ids, attention_mask=attention_mask).logits
        preds = torch.argmax(logits, dim=1)
        all_preds.extend(preds.cpu().numpy())
        all_labels.extend(labels.cpu().numpy())

# Calculate classification report
report = classification_report(all_labels, all_preds, target_names=['Positive', 'Negative', 'Neutral'])
print()
print("Roberta Classification Report:")
print(report)

Epoch 1: 100%|██████████| 38/38 [07:52<00:00, 12.44s/batches]


Epoch 1, Loss: 0.6791262752131412


Epoch 2: 100%|██████████| 38/38 [07:27<00:00, 11.78s/batches]


Epoch 2, Loss: 0.410270009385912


Epoch 3: 100%|██████████| 38/38 [07:37<00:00, 12.05s/batches]


Epoch 3, Loss: 0.2327821580202956


Evaluation: 100%|██████████| 10/10 [00:32<00:00,  3.25s/batches]


Roberta Classification Report:
              precision    recall  f1-score   support

    Positive       0.67      0.93      0.78        95
    Negative       0.88      0.52      0.66       109
     Neutral       0.87      0.95      0.91        95

    accuracy                           0.79       299
   macro avg       0.81      0.80      0.78       299
weighted avg       0.81      0.79      0.78       299



In [22]:
# Definition of the labels
labels_definition = config.id2label
print("Labels Definition:", labels_definition)

Labels Definition: {0: 'negative', 1: 'neutral', 2: 'positive'}


In [12]:
# Define a class for data preparation
class SimpleDataset(torch.utils.data.Dataset):
    def __init__(self, tokenized_texts):
        self.tokenized_texts = tokenized_texts

    def __len__(self):
        return len(self.tokenized_texts["input_ids"])

    def __getitem__(self, idx):
        return {k: v[idx] for k, v in self.tokenized_texts.items()}

# Tokenize texts and create prediction dataset
def tokenize_texts(texts):
    tokenized_texts = tokenizer(texts, truncation=True, padding=True, max_length=128, return_tensors="pt")
    return SimpleDataset(tokenized_texts)

# Perform inference and transform predictions to labels
def predict_sentiment(texts):
    # Tokenize texts
    pred_dataset = tokenize_texts(texts)

    # Set up trainer for inference
    training_args = TrainingArguments(
        output_dir="./dummy_output_dir",  # Provide a dummy output directory
        per_device_eval_batch_size=8,   # Reduce batch size
        disable_tqdm=False,             # Enable tqdm progress bars
    )
    trainer = Trainer(
        model=model,
        args=training_args,
    )

    # Perform inference
    predictions = trainer.predict(pred_dataset)
    preds = predictions.predictions.argmax(-1)
    labels = pd.Series(preds).map(model.config.id2label)

    # Convert predictions to PyTorch tensor
    predictions_tensor = torch.tensor(predictions.predictions)

    # Calculate softmax scores
    scores = (torch.exp(predictions_tensor) / torch.exp(predictions_tensor).sum(-1, keepdim=True)).max(1)

    return labels, scores

# Example usage with 'cleaned_tweet' column
tweets = data['cleaned_tweet'].tolist()

# Calculate the total number of batches
batch_size = 64
total_batches = (len(tweets) + batch_size - 1) // batch_size

# Perform sentiment analysis in batches
labels, scores = [], []
for i in tqdm(range(total_batches)):
    start_idx = i * batch_size
    end_idx = min((i + 1) * batch_size, len(tweets))
    batch_tweets = tweets[start_idx:end_idx]
    batch_labels, batch_scores = predict_sentiment(batch_tweets)
    labels.extend(batch_labels)
    scores.extend(batch_scores)


Some weights of the model checkpoint at cardiffnlp/twitter-roberta-base-sentiment-latest were not used when initializing RobertaForSequenceClassification: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
  0%|          | 0/4488 [00:00<?, ?it/s]/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches'

  0%|          | 1/4488 [00:03<4:05:14,  3.28s/it]/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


  0%|          | 2/4488 [00:03<1:54:19,  1.53s/it]/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


  0%|          | 3/4488 [00:03<1:13:57,  1.01it/s]/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


  0%|          | 4/4488 [00:04<56:57,  1.31it/s]  /usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


...

100%|█████████▉| 4484/4488 [23:24<00:01,  3.44it/s]/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


100%|█████████▉| 4485/4488 [23:25<00:00,  3.30it/s]/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


100%|█████████▉| 4486/4488 [23:25<00:00,  3.32it/s]/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


100%|█████████▉| 4487/4488 [23:25<00:00,  3.38it/s]/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


100%|██████████| 4488/4488 [23:26<00:00,  3.19it/s]


In [15]:
# Definition of the labels
labels_definition = config.id2label
print("Labels Definition:", labels_definition)

Labels Definition: {0: 'negative', 1: 'neutral', 2: 'positive'}


In [16]:
data['predicted_sentiment'] = labels

In [17]:
data.to_csv("predicted_sentiments_data.csv", index=False)
# data['predicted_sentiment'] = data['predicted_sentiment'].map({'positive': 2, 'neutral': 1, 'negative': 0})